In [1]:
import numpy as np
import pandas as pd
import plotly.express as px
import plotly.graph_objects as go
from sklearn.preprocessing import MinMaxScaler

mi target será la variable sales, significa cantidad de ventas en ese dia

Exogenas:

* Dia de la semana
* feriados
* tipo (store)
* cluster (store)

## Tablas

### train

In [2]:
#df_train= pd.read_csv(r'D:\Escritorio\IES21\4to cuatrimestre\PP2\data\train.csv')
df_train= pd.read_csv(r'C:\Users\Usuario\Desktop\lautaro\ies 21\IES21\4to cuatrimestre\PP2\data\train.csv')
df_train.head()

id        date  store_nbr      family  sales  onpromotion
0   0  2013-01-01          1  AUTOMOTIVE    0.0            0
1   1  2013-01-01          1   BABY CARE    0.0            0
2   2  2013-01-01          1      BEAUTY    0.0            0
3   3  2013-01-01          1   BEVERAGES    0.0            0
4   4  2013-01-01          1       BOOKS    0.0            0

In [3]:
#Podemos observar que no tenemos datos nulos en todo nuestro DataSet
df_train.isnull().sum()

id             0
date           0
store_nbr      0
family         0
sales          0
onpromotion    0
dtype: int64

In [4]:
df_train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3000888 entries, 0 to 3000887
Data columns (total 6 columns):
 #   Column       Dtype  
---  ------       -----  
 0   id           int64  
 1   date         object 
 2   store_nbr    int64  
 3   family       object 
 4   sales        float64
 5   onpromotion  int64  
dtypes: float64(1), int64(3), object(2)
memory usage: 137.4+ MB


In [5]:
#Para facilitar el trabajo con las fechas, pasamos la columna date a tipo datetime
df_train['date']=pd.to_datetime(df_train['date'])

### Test (usar para testear)

In [6]:
#df_test= pd.read_csv(r'D:\Escritorio\IES21\4to cuatrimestre\PP2\data\test.csv')
df_test= pd.read_csv('c:/Users/Usuario/Desktop/lautaro/ies 21/IES21/4to cuatrimestre/PP2/data/test.csv')
df_test

id        date  store_nbr                      family  onpromotion
0      3000888  2017-08-16          1                  AUTOMOTIVE            0
1      3000889  2017-08-16          1                   BABY CARE            0
2      3000890  2017-08-16          1                      BEAUTY            2
3      3000891  2017-08-16          1                   BEVERAGES           20
4      3000892  2017-08-16          1                       BOOKS            0
...        ...         ...        ...                         ...          ...
28507  3029395  2017-08-31          9                     POULTRY            1
28508  3029396  2017-08-31          9              PREPARED FOODS            0
28509  3029397  2017-08-31          9                     PRODUCE            1
28510  3029398  2017-08-31          9  SCHOOL AND OFFICE SUPPLIES            9
28511  3029399  2017-08-31          9                     SEAFOOD            0

[28512 rows x 5 columns]

### Tiendas

In [7]:
#df_store= pd.read_csv(r'D:\Escritorio\IES21\4to cuatrimestre\PP2\data\stores.csv')
df_store= pd.read_csv('c:/Users/Usuario/Desktop/lautaro/ies 21/IES21/4to cuatrimestre/PP2/data/stores.csv')
df_store.head()

store_nbr           city                           state type  cluster
0          1          Quito                       Pichincha    D       13
1          2          Quito                       Pichincha    D       13
2          3          Quito                       Pichincha    D        8
3          4          Quito                       Pichincha    D        9
4          5  Santo Domingo  Santo Domingo de los Tsachilas    D        4

In [8]:
# Cantidad de tiendas
df_store['store_nbr'].count()

54

In [9]:
df_store.loc[df_store['type']=='B']

store_nbr           city                           state type  cluster
8           9          Quito                       Pichincha    B        6
10         11        Cayambe                       Pichincha    B        6
17         18          Quito                       Pichincha    B       16
19         20          Quito                       Pichincha    B        6
20         21  Santo Domingo  Santo Domingo de los Tsachilas    B        6
30         31       Babahoyo                        Los Rios    B       10
33         34      Guayaquil                          Guayas    B        6
38         39         Cuenca                           Azuay    B        6

In [10]:
df_store['cluster'].unique()

array([13,  8,  9,  4,  6, 15,  7,  3, 12, 16,  1, 10,  2,  5, 11, 14, 17],
      dtype=int64)

In [11]:
df_store['type'].unique()

array(['D', 'B', 'C', 'E', 'A'], dtype=object)

### Dias Feriados

In [12]:
#df_holidays_events= pd.read_csv(r'D:\Escritorio\IES21\4to cuatrimestre\PP2\data\holidays_events.csv')
df_holidays_events= pd.read_csv('c:/Users/Usuario/Desktop/lautaro/ies 21/IES21/4to cuatrimestre/PP2/data/holidays_events.csv')
df_holidays_events.head()

date     type    locale locale_name                    description  \
0  2012-03-02  Holiday     Local       Manta             Fundacion de Manta   
1  2012-04-01  Holiday  Regional    Cotopaxi  Provincializacion de Cotopaxi   
2  2012-04-12  Holiday     Local      Cuenca            Fundacion de Cuenca   
3  2012-04-14  Holiday     Local    Libertad      Cantonizacion de Libertad   
4  2012-04-21  Holiday     Local    Riobamba      Cantonizacion de Riobamba   

   transferred  
0        False  
1        False  
2        False  
3        False  
4        False

In [13]:
df_holidays_events=df_holidays_events.loc[df_holidays_events['type']=='Holiday']
df_holidays_events['date']=pd.to_datetime(df_holidays_events['date'])
df_holidays_events

date     type    locale locale_name                    description  \
0   2012-03-02  Holiday     Local       Manta             Fundacion de Manta   
1   2012-04-01  Holiday  Regional    Cotopaxi  Provincializacion de Cotopaxi   
2   2012-04-12  Holiday     Local      Cuenca            Fundacion de Cuenca   
3   2012-04-14  Holiday     Local    Libertad      Cantonizacion de Libertad   
4   2012-04-21  Holiday     Local    Riobamba      Cantonizacion de Riobamba   
..         ...      ...       ...         ...                            ...   
338 2017-11-12  Holiday     Local      Ambato        Independencia de Ambato   
340 2017-12-06  Holiday     Local       Quito             Fundacion de Quito   
341 2017-12-08  Holiday     Local        Loja              Fundacion de Loja   
344 2017-12-22  Holiday     Local     Salinas       Cantonizacion de Salinas   
348 2017-12-25  Holiday  National     Ecuador                        Navidad   

     transferred  
0          False  
1          False  
2          False  
3          False  
4          False  
..           ...  
338        False  
340         True  
341        False  
344        False  
348        False  

[221 rows x 6 columns]

### Precio petroleo

In [14]:
#df_oil= pd.read_csv(r'D:\Escritorio\IES21\4to cuatrimestre\PP2\data\oil.csv')
df_oil= pd.read_csv('c:/Users/Usuario/Desktop/lautaro/ies 21/IES21/4to cuatrimestre/PP2/data/oil.csv')
df_oil.head()

date  dcoilwtico
0  2013-01-01         NaN
1  2013-01-02       93.14
2  2013-01-03       92.97
3  2013-01-04       93.12
4  2013-01-07       93.20

In [15]:
df_oil.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1218 entries, 0 to 1217
Data columns (total 2 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   date        1218 non-null   object 
 1   dcoilwtico  1175 non-null   float64
dtypes: float64(1), object(1)
memory usage: 19.2+ KB


In [16]:
df_oil['date']=pd.to_datetime(df_oil['date'])

## EDA

### Cant de ventas

##### Por dia

In [17]:
# Agrupo por columna date y famili, sumando sales de las diferentes stores
df_cant_ventas=df_train.groupby(['date','family'])['sales'].sum().reset_index()
# Pongo a date como indice para usar una herramienta en un futuro
df_cant_ventas.index= df_cant_ventas['date']
df_cant_ventas.head()

date      family  sales
date                                    
2013-01-01 2013-01-01  AUTOMOTIVE    0.0
2013-01-01 2013-01-01   BABY CARE    0.0
2013-01-01 2013-01-01      BEAUTY    2.0
2013-01-01 2013-01-01   BEVERAGES  810.0
2013-01-01 2013-01-01       BOOKS    0.0

In [18]:
import plotly.express as px
fig = px.line(df_cant_ventas, x=df_cant_ventas.index, y='sales',color='family')
fig.show()

Se puede observar que todos los 1 de enero, indeferente al año, no se realizan casi ventas

##### Por semanas

In [19]:
# Agrupo el DataFrame df_cant_ventas por semana, promediando sus valores
df_cant_ventas_semana=df_cant_ventas.resample('MS').mean()
df_cant_ventas_semana.head()

sales
date                    
2013-01-01  10095.429850
2013-02-01  10453.419673
2013-03-01  11171.551356
2013-04-01  11104.509836
2013-05-01  11336.954064

In [20]:
import plotly.express as px
fig = px.line(df_cant_ventas_semana, x=df_cant_ventas_semana.index, y='sales')
fig.show()

Otro análisis sin considerar la familia y agrupados por semanas, se puede observar que con el paso del tiempo, se fueron realizando mas ventas

### Precio del petroleo a lo largo del tiempo

In [21]:
import plotly.express as px
fig = px.line(df_oil, x='date', y='dcoilwtico')
fig.show()

Se observa que con el tiempo, el precio del peotroleo fue desendiendo, tambien se aprecia que hay varios dias donde no se cuenta con los datos del precio de petroleo, se imputaran en un futuro.

### Relacion cantidad de ventas y precio del petroleo

In [22]:
df_grupo= df_train.groupby(['date'])['sales'].sum().reset_index()
df_grupo.head()

date          sales
0 2013-01-01    2511.618999
1 2013-01-02  496092.417944
2 2013-01-03  361461.231124
3 2013-01-04  354459.677093
4 2013-01-05  477350.121229

In [23]:
df_grupo= pd.merge(df_grupo,df_oil, on='date')
df_grupo.head()

date          sales  dcoilwtico
0 2013-01-01    2511.618999         NaN
1 2013-01-02  496092.417944       93.14
2 2013-01-03  361461.231124       92.97
3 2013-01-04  354459.677093       93.12
4 2013-01-07  336122.801066       93.20

In [24]:
df_grupo=df_grupo.fillna(method='bfill')
df_grupo.head()

date          sales  dcoilwtico
0 2013-01-01    2511.618999       93.14
1 2013-01-02  496092.417944       93.14
2 2013-01-03  361461.231124       92.97
3 2013-01-04  354459.677093       93.12
4 2013-01-07  336122.801066       93.20

In [25]:
x= df_grupo.drop('date',axis=1)
from sklearn.preprocessing import MinMaxScaler
scaler = MinMaxScaler()
scaler.fit(x)
transformado=scaler.transform(x)
dftransf= pd.DataFrame(transformado, columns=['sales','dcoilwtico'])
dftransf['date']=df_grupo[['date']]
dftransf.head()

sales  dcoilwtico       date
0  0.000000    0.792965 2013-01-01
1  0.352609    0.792965 2013-01-02
2  0.256430    0.790951 2013-01-03
3  0.251428    0.792728 2013-01-04
4  0.238329    0.793675 2013-01-07

In [26]:

fig = go.Figure()

fig.add_trace(go.Scatter(x=dftransf['date'], y=dftransf['sales'], name='Sales', line=dict(color='firebrick', width=2)))

fig.add_trace(go.Scatter(x=dftransf['date'], y=dftransf['dcoilwtico'], name='Oil', line=dict(color='royalblue', width=2)))

fig.update_layout(title='Relacion de la cantidad total de ventas con precio de petroleo',
                   xaxis_title='Date')
fig.show()

se aprecia qeue a medida que el precio del petroleo fue disminuyendo, la cantidad de ventas iban aumentando, esta relacion sucede mientras avanzamos en el tiempo.

## DataSet para entrenar

In [27]:
df_final=pd.merge(df_train,df_oil,on='date',how='left')
df_final=df_final.fillna(method='bfill')
df_final=pd.merge(df_final,df_holidays_events,on='date',how='left')
df_final=df_final.merge(df_store,on='store_nbr')
df_final.loc[(df_final['type_x'].isna()),'type_x'] = 'Common Day'
df_final.drop(['locale','locale_name','description','transferred','city','state'],axis=1,inplace=True)
df_final

id       date  store_nbr                      family     sales  \
0              0 2013-01-01          1                  AUTOMOTIVE     0.000   
1              1 2013-01-01          1                   BABY CARE     0.000   
2              2 2013-01-01          1                      BEAUTY     0.000   
3              3 2013-01-01          1                   BEVERAGES     0.000   
4              4 2013-01-01          1                       BOOKS     0.000   
...          ...        ...        ...                         ...       ...   
3029395  3000883 2017-08-15          9                     POULTRY   438.133   
3029396  3000884 2017-08-15          9              PREPARED FOODS   154.553   
3029397  3000885 2017-08-15          9                     PRODUCE  2419.729   
3029398  3000886 2017-08-15          9  SCHOOL AND OFFICE SUPPLIES   121.000   
3029399  3000887 2017-08-15          9                     SEAFOOD    16.000   

         onpromotion  dcoilwtico   type_x type_y  cluster  
0                  0       93.14  Holiday      D       13  
1                  0       93.14  Holiday      D       13  
2                  0       93.14  Holiday      D       13  
3                  0       93.14  Holiday      D       13  
4                  0       93.14  Holiday      D       13  
...              ...         ...      ...    ...      ...  
3029395            0       47.57  Holiday      B        6  
3029396            1       47.57  Holiday      B        6  
3029397          148       47.57  Holiday      B        6  
3029398            8       47.57  Holiday      B        6  
3029399            0       47.57  Holiday      B        6  

[3029400 rows x 10 columns]

In [28]:
df_final["type_x"] = df_final["type_x"].map({"Holiday": 1, "Common Day": 2})
df_final["type_y"] = df_final["type_y"].map({"A": 1, "B": 2, "C": 3, "D": 4, "E": 5,})
df_final.replace(list(df_final['family'].unique()), list(np.arange(0,len(list(df_final['family'].unique())))),inplace=True)

In [29]:
df_final=df_final.set_index('date')
df_final

id  store_nbr  family     sales  onpromotion  dcoilwtico  \
date                                                                        
2013-01-01        0          1       0     0.000            0       93.14   
2013-01-01        1          1       1     0.000            0       93.14   
2013-01-01        2          1       2     0.000            0       93.14   
2013-01-01        3          1       3     0.000            0       93.14   
2013-01-01        4          1       4     0.000            0       93.14   
...             ...        ...     ...       ...          ...         ...   
2017-08-15  3000883          9      28   438.133            0       47.57   
2017-08-15  3000884          9      29   154.553            1       47.57   
2017-08-15  3000885          9      30  2419.729          148       47.57   
2017-08-15  3000886          9      31   121.000            8       47.57   
2017-08-15  3000887          9      32    16.000            0       47.57   

            type_x  type_y  cluster  
date                                 
2013-01-01       1       4       13  
2013-01-01       1       4       13  
2013-01-01       1       4       13  
2013-01-01       1       4       13  
2013-01-01       1       4       13  
...            ...     ...      ...  
2017-08-15       1       2        6  
2017-08-15       1       2        6  
2017-08-15       1       2        6  
2017-08-15       1       2        6  
2017-08-15       1       2        6  

[3029400 rows x 9 columns]

In [30]:
df_family_AUTO= df_final.loc[(df_final['store_nbr']==1) & (df_final['family']==0)]
df_family_AUTO.drop(['id','store_nbr','family'],axis=1,inplace=True)
df_family_AUTO=df_family_AUTO.resample('D').mean()
df_family_AUTO=df_family_AUTO.fillna(0)

C:\Users\Usuario\AppData\Local\Temp\ipykernel_12744\3003529259.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



## Modelado

In [31]:
from sklearn.ensemble import RandomForestRegressor
from sklearn.metrics import mean_squared_error
from skforecast.ForecasterAutoreg import ForecasterAutoreg
from skforecast.model_selection import grid_search_forecaster

c:\Users\Usuario\Desktop\lautaro\ies 21\IES21\4to cuatrimestre\PP2\entorno\lib\site-packages\tqdm\auto.py:22: TqdmWarning:

IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html



In [32]:
steps=15
datos_train= df_family_AUTO[:-steps]
datos_test= df_family_AUTO[-steps:]

In [33]:
datos_train

sales  onpromotion  dcoilwtico  type_x  type_y  cluster
date                                                               
2013-01-01    0.0          0.0       93.14     1.0     4.0     13.0
2013-01-02    2.0          0.0       93.14     2.0     4.0     13.0
2013-01-03    3.0          0.0       92.97     2.0     4.0     13.0
2013-01-04    3.0          0.0       93.12     2.0     4.0     13.0
2013-01-05    5.0          0.0       93.20     2.0     4.0     13.0
...           ...          ...         ...     ...     ...      ...
2017-07-27    5.0          0.0       49.05     2.0     4.0     13.0
2017-07-28    7.0          0.0       49.72     2.0     4.0     13.0
2017-07-29    4.0          0.0       50.21     2.0     4.0     13.0
2017-07-30    1.0          0.0       50.21     2.0     4.0     13.0
2017-07-31    8.0          0.0       50.21     2.0     4.0     13.0

[1673 rows x 6 columns]

In [34]:
datos_test

sales  onpromotion  dcoilwtico  type_x  type_y  cluster
date                                                               
2017-08-01    5.0          0.0       49.19     2.0     4.0     13.0
2017-08-02    4.0          0.0       49.60     2.0     4.0     13.0
2017-08-03    3.0          0.0       49.03     2.0     4.0     13.0
2017-08-04    8.0          0.0       49.57     2.0     4.0     13.0
2017-08-05    5.0          0.0       49.37     1.0     4.0     13.0
2017-08-06    6.0          0.0       49.37     2.0     4.0     13.0
2017-08-07    7.0          0.0       49.37     2.0     4.0     13.0
2017-08-08    4.0          0.0       49.07     2.0     4.0     13.0
2017-08-09    7.0          0.0       49.59     2.0     4.0     13.0
2017-08-10    9.0          0.0       48.54     1.0     4.0     13.0
2017-08-11    1.0          0.0       48.81     2.0     4.0     13.0
2017-08-12    6.0          0.0       47.59     2.0     4.0     13.0
2017-08-13    1.0          0.0       47.59     2.0     4.0     13.0
2017-08-14    1.0          0.0       47.59     2.0     4.0     13.0
2017-08-15    4.0          0.0       47.57     1.0     4.0     13.0

### Modelo puro

In [35]:
forecaster = ForecasterAutoreg(
                regressor = RandomForestRegressor(random_state=123),
                lags      = 8
             )

forecaster.fit(y=datos_train['sales'], exog=datos_train[['onpromotion','dcoilwtico','type_x','type_y','cluster']])
forecaster

ForecasterAutoreg 
Regressor: RandomForestRegressor(random_state=123) 
Lags: [1 2 3 4 5 6 7 8] 
Transformer for y: None 
Transformer for exog: None 
Window size: 8 
Included exogenous: True 
Type of exogenous variable: <class 'pandas.core.frame.DataFrame'> 
Exogenous variables names: ['onpromotion', 'dcoilwtico', 'type_x', 'type_y', 'cluster'] 
Training range: [Timestamp('2013-01-01 00:00:00'), Timestamp('2017-07-31 00:00:00')] 
Training index type: DatetimeIndex 
Training index frequency: D 
Regressor parameters: {'bootstrap': True, 'ccp_alpha': 0.0, 'criterion': 'squared_error', 'max_depth': None, 'max_features': 1.0, 'max_leaf_nodes': None, 'max_samples': None, 'min_impurity_decrease': 0.0, 'min_samples_leaf': 1, 'min_samples_split': 2, 'min_weight_fraction_leaf': 0.0, 'n_estimators': 100, 'n_jobs': None, 'oob_score': False, 'random_state': 123, 'verbose': 0, 'warm_start': False} 
Creation date: 2022-11-08 14:32:41 
Last fit date: 2022-11-08 14:32:44 
Skforecast version: 0.5.1 
Pyth

In [36]:
predicciones = forecaster.predict(steps=steps, exog=datos_train[['onpromotion','dcoilwtico','type_x','type_y','cluster']])

In [37]:
error_mse = mean_squared_error(
                y_true = datos_test['sales'],
                y_pred = predicciones
            )

print(f"Error de test (mse): {error_mse}")

Error de test (mse): 11.414306666666668


### Hiperparameros

In [38]:
steps=15
forecaster = ForecasterAutoreg(
                regressor = RandomForestRegressor(random_state=123),
                lags      = 12 # Este valor será remplazado en el grid search
             )

lags_grid = [60,70,80]

param_grid = {'n_estimators': [900,1000,1100],
              'max_depth': [35,40,45]}

resultados_grid = grid_search_forecaster(
                        forecaster         = forecaster,
                        y                  = datos_train['sales'],
                        exog               = datos_train['dcoilwtico'],
                        param_grid         = param_grid,
                        lags_grid          = lags_grid,
                        steps              = steps,
                        refit              = False,
                        metric             = 'mean_squared_error',
                        initial_train_size = int(len(datos_train)*0.5),
                        fixed_train_size   = False,
                        return_best        = True,
                        verbose            = False
                    )

Number of models compared: 27.


loop lags_grid:  67%|███████████████████████▎           | 2/3 [1:05:11<32:21, 1941.10s/it]

In [65]:
resultados_grid

array([1, 2, 3, 4, 5])

In [ ]:
predicciones = forecaster.predict(steps=steps, exog=datos_test[['onpromotion','dcoilwtico','type_x','type_y','cluster']])

c:\Users\Usuario\Desktop\lautaro\ies 21\IES21\4to cuatrimestre\PP2\env\lib\site-packages\skforecast\utils\utils.py:474: UserWarning:

`exog` has DatetimeIndex index but no frequency. Index is overwritten with a RangeIndex of step 1.

c:\Users\Usuario\Desktop\lautaro\ies 21\IES21\4to cuatrimestre\PP2\env\lib\site-packages\skforecast\utils\utils.py:417: UserWarning:

`last_window` has DatetimeIndex index but no frequency. Index is overwritten with a RangeIndex of step 1.



In [ ]:
error_mse = mean_squared_error(y_true = datos_test['sales'], y_pred = predicciones)
print(f"Error de test (mse) {error_mse}")

Error de test (mse) 6.452640141487137


In [ ]:
predicciones

2017-08-01    3.25
2017-08-02    2.03
2017-08-03    3.03
2017-08-04    2.67
2017-08-05    4.20
2017-08-06    2.71
2017-08-07    3.03
2017-08-08    2.48
2017-08-09    1.82
2017-08-10    2.60
2017-08-11    2.56
2017-08-12    2.33
2017-08-13    2.58
2017-08-14    2.41
2017-08-15    1.53
Freq: D, Name: pred, dtype: float64

In [ ]:
datos_test['sales']

date
2017-08-01    5.0
2017-08-02    4.0
2017-08-03    3.0
2017-08-04    8.0
2017-08-05    5.0
2017-08-06    6.0
2017-08-07    7.0
2017-08-08    4.0
2017-08-09    7.0
2017-08-10    9.0
2017-08-11    1.0
2017-08-12    6.0
2017-08-13    1.0
2017-08-14    1.0
2017-08-15    4.0
Freq: D, Name: sales, dtype: float64

In [ ]:
fig = go.Figure()

fig.add_trace(go.Scatter(x=datos_test.index, y=datos_test['sales'], name='Test', line=dict(color='firebrick', width=2)))

fig.add_trace(go.Scatter(x=predicciones.index, y=predicciones, name='prediccion', line=dict(color='royalblue', width=2)))

fig.show()